# Overview
This is a playground notebook for exploring the NAEI Point Source data. The data is available from the [UK Government website](https://data.gov.uk/dataset/aecc3f3e-3f0c-4e2e-9b1c-6f8d5f2d1f0a/naei-point-source-data).
The plan is to develop in the notebook and then move to a script for a smoother and more systematic approach to launching the application. The idea is to see what I can do with this data, I haven't gone into this with any one specific goal in mind but some things I'd like to address:
1. Time Series Analysis of Emissions and mapping key pollutants
2. Time Series Forecasting inline with Net Zero Goals
3. Correlation with other datasets, nothing particular but maybe:
    - Weather Data
    - Health Data
    - Economic Data
4. Geospatial Analysis and Mapping

# 0. Introduction and Setup
## 0.0 Installs

In [45]:
import pandas as pd
import numpy as np
import os
import geopandas as gpd
from shapely.geometry import Point, box
import plotly.express as px
from IPython.display import display, clear_output
import ipywidgets as widgets

## 0.1 Load the Data
Lets load the data nad get some 

In [46]:
file = "NAEIPointsSources_2023.xlsx"
current_dir = os.getcwd()
file_path = os.path.join(current_dir, file)

In [47]:
xls = pd.ExcelFile(file_path, engine="openpyxl")  # XLSX file
sheets = xls.sheet_names
print("sheets:", xls.sheet_names)

sheets: ['QA', 'Description', 'Air Toxic', 'GHGs', 'Heavy Metals', 'Multi Effect', 'PAHs', 'POPs', 'ESRI_MAPINFO_SHEET']


In [48]:
df = pd.read_excel(xls, sheet_name=sheets[3], engine="openpyxl")
df.head()

Year  PollutantID            Pollutant_Name  PlantID           Site  \
0  2005            2  Carbon Dioxide as Carbon       25       Coventry   
1  2005            2  Carbon Dioxide as Carbon       28        Spondon   
2  2005            2  Carbon Dioxide as Carbon       84  Middlesbrough   
3  2005            2  Carbon Dioxide as Carbon      124      Rogestone   
4  2005            2  Carbon Dioxide as Carbon      156     Seal Sands   

   Easting  Northing                       Operator  SectorID  \
0   434800    282300  Acordis Acetate Chemicals Ltd        10   
1   439600    336000  Acordis Acetate Chemicals Ltd        10   
2   458190    520340               Air Products Plc         3   
3   326560    187930       Alcan Rolled Products UK        14   
4   452150    524260  Amoco (UK) Exploration Co Ltd         3   

                                 Sector      Emission    Unit  Country  \
0                     Chemical industry   9490.909091  Tonnes  England   
1                     Chemical industry   1767.086904  Tonnes  England   
2  Oil & gas exploration and production  22854.545450  Tonnes  England   
3          Non-ferrous metal industries   5184.545455  Tonnes    Wales   
4  Oil & gas exploration and production  15116.771740  Tonnes  England   

  Datatype  
0        O  
1        O  
2        O  
3        O  
4        O

## 0.2 Clean-Up
So Pollutant_Name is pretty messy so lets put this in a nicer format for analysis, likewise, the coordinates are in easting and northing so lets convert that to something more useful like lat and long.
I'll also want to drop any null rows and I can modify the "Emission" column to multiply by the GWP.

In [49]:
if 'Pollutant_Name' in df.columns:  # check if the column exists
    # normalize specific names
    rename_map = {
        "Nitrous Oxide": "N20",
        "Methane": "CH3",
        "Carbon Dioxide": "CO2",
        "Carbon Dioxide as Carbon": "CO2",
        "Carbon": "CO2"
    }
    df['Pollutant_Name'] = df['Pollutant_Name'].replace(rename_map)

    # GWP (AR5) mapping
    gwp_map = {"CO2": 1, "CH3": 28, "N20": 265}
    df['GWP'] = df['Pollutant_Name'].map(gwp_map)

    uniques = df['Pollutant_Name'].dropna().unique()
    print("unique pollutant count:", len(uniques))
    print(uniques)
else:
    print("Column 'Pollutant_Name' not found. Available columns:", df.columns.tolist())

unique pollutant count: 2
['CO2' 'N20']


In [50]:
if {'Easting', 'Northing'}.issubset(df.columns):
    # coerce to numeric (non-numeric -> NaN)
    e = pd.to_numeric(df['Easting'], errors='coerce')
    n = pd.to_numeric(df['Northing'], errors='coerce')

    valid = e.notna() & n.notna()
    if valid.any():
        # build GeoDataFrame only for valid rows
        valid_idx = df.index[valid]
        geom = [Point(x, y) for x, y in zip(e[valid], n[valid])]
        gdf = gpd.GeoDataFrame(df.loc[valid_idx].copy(), geometry=geom, crs="EPSG:27700")

        # project to WGS84
        gdf = gdf.to_crs("EPSG:4326")

        # write lat/lon back to original DataFrame
        df.loc[valid_idx, "Longitude"] = gdf.geometry.x.values
        df.loc[valid_idx, "Latitude"] = gdf.geometry.y.values

        print(f"Converted {valid.sum()} rows from EPSG:27700 to EPSG:4326 and added 'Latitude'/'Longitude'.")
    else:
        print("No valid numeric Easting/Northing values found.")
else:
    print("Required columns 'Easting' and 'Northing' not found. Available columns:", df.columns.tolist())

Converted 67062 rows from EPSG:27700 to EPSG:4326 and added 'Latitude'/'Longitude'.


In [51]:
df["Emissions_GWP"] = df["Emission"] * df["GWP"]

In [52]:
n_rows, n_cols = df.shape
na_counts = df.isna().sum().sum()

print(f"Before: rows={n_rows}, cols={n_cols}")
print("Initial total NA values:", int(na_counts))

df = df.dropna(inplace=False)

print(f"After dropna: rows={df.shape[0]}, cols={df.shape[1]}")
remaining_total_na = df.isna().sum().sum()
print("Remaining total NA values:", int(remaining_total_na))

Before: rows=67062, cols=18
Initial total NA values: 30
After dropna: rows=67032, cols=18
Remaining total NA values: 0


In [53]:
ignore = ["PollutantID", "Pollutant_Name", "Emissions_GWP", "GWP", "Emission"]
group_cols = [c for c in df.columns if c not in ignore]

# build aggregation dict dynamically
agg_dict = {"Emissions_GWP": "sum"}
for col in ["Pollutant_Name", "PollutantID"]:
    if col in df.columns:
        # join unique non-null values (as strings)
        agg_dict[col] = (lambda s, col=col: ",".join(sorted(set(s.dropna().astype(str)))))

# perform grouping
df_aggregated = df.groupby(group_cols, dropna=False, as_index=False).agg(agg_dict)
df_aggregated.drop(columns=["PollutantID","Pollutant_Name","GWP"], inplace=True, errors='ignore')

print(f"Original rows: {len(df)}, Aggregated rows: {len(df_aggregated)}")
df_aggregated.head()

Original rows: 67032, Aggregated rows: 59485


Year  PlantID        Site  Easting  Northing  \
0  2005       25    Coventry   434800    282300   
1  2005       25    Coventry   434800    282300   
2  2005       28     Spondon   439600    336000   
3  2005       28     Spondon   439600    336000   
4  2005       36  Bedlington   429190    584910   

                        Operator  SectorID             Sector    Unit  \
0  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
1  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
2  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
3  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
4              ACS Dobfar UK Ltd        10  Chemical industry  Tonnes   

   Country Datatype  Longitude   Latitude  Emissions_GWP  
0  England        M  -1.489511  52.437588      16.996331  
1  England        O  -1.489511  52.437588    9490.909091  
2  England        M  -1.412473  52.919983       3.042279  
3  England        O  -1.412473  52.919983    1767.086904  
4  England        O  -1.543450  55.157669     793.496066

## 0.3 Final Check for Introduction
Last check and make sure the dataframe is in a nice format

In [54]:
df.head()

Year  PollutantID Pollutant_Name  PlantID           Site  Easting  \
0  2005            2            CO2       25       Coventry   434800   
1  2005            2            CO2       28        Spondon   439600   
2  2005            2            CO2       84  Middlesbrough   458190   
3  2005            2            CO2      124      Rogestone   326560   
4  2005            2            CO2      156     Seal Sands   452150   

   Northing                       Operator  SectorID  \
0    282300  Acordis Acetate Chemicals Ltd        10   
1    336000  Acordis Acetate Chemicals Ltd        10   
2    520340               Air Products Plc         3   
3    187930       Alcan Rolled Products UK        14   
4    524260  Amoco (UK) Exploration Co Ltd         3   

                                 Sector      Emission    Unit  Country  \
0                     Chemical industry   9490.909091  Tonnes  England   
1                     Chemical industry   1767.086904  Tonnes  England   
2  Oil & gas exploration and production  22854.545450  Tonnes  England   
3          Non-ferrous metal industries   5184.545455  Tonnes    Wales   
4  Oil & gas exploration and production  15116.771740  Tonnes  England   

  Datatype  GWP  Longitude   Latitude  Emissions_GWP  
0        O    1  -1.489511  52.437588    9490.909091  
1        O    1  -1.412473  52.919983    1767.086904  
2        O    1  -1.101369  54.574948   22854.545450  
3        O    1  -3.061387  51.585423    5184.545455  
4        O    1  -1.194097  54.610829   15116.771740

In [55]:
df_aggregated.head()

Year  PlantID        Site  Easting  Northing  \
0  2005       25    Coventry   434800    282300   
1  2005       25    Coventry   434800    282300   
2  2005       28     Spondon   439600    336000   
3  2005       28     Spondon   439600    336000   
4  2005       36  Bedlington   429190    584910   

                        Operator  SectorID             Sector    Unit  \
0  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
1  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
2  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
3  Acordis Acetate Chemicals Ltd        10  Chemical industry  Tonnes   
4              ACS Dobfar UK Ltd        10  Chemical industry  Tonnes   

   Country Datatype  Longitude   Latitude  Emissions_GWP  
0  England        M  -1.489511  52.437588      16.996331  
1  England        O  -1.489511  52.437588    9490.909091  
2  England        M  -1.412473  52.919983       3.042279  
3  England        O  -1.412473  52.919983    1767.086904  
4  England        O  -1.543450  55.157669     793.496066

# 1. Exploratory Data Analysis
Let's probe and see what we can see.
## 1.0 Spatial Analysis
Let's just look at in on a map basis first, may be best for visualising how this looks.

In [56]:
# prepare dataframe with valid coordinates
df_map = df_aggregated.dropna(subset=["Latitude", "Longitude"]).copy()
if df_map.empty:
    raise ValueError("No rows with valid 'Latitude' and 'Longitude' to plot.")

# choose hover columns present in the DF
hover_cols = [c for c in ["Site", "Pollutant_Name", "GWP", "Emissions"] if c in df_map.columns]

center={'lat':56.0, 'lon':-3.0}  # centered on UK

# choose color source and optionally use a log transform to avoid saturation
color_col = "Emissions_GWP" if "Emissions_GWP" in df_map.columns else ("Emissions" if "Emissions" in df_map.columns else None)
if color_col is None:
    color_col = hover_cols[0] if hover_cols else None

# create a log-transformed color column if values are highly skewed
if color_col is not None and pd.api.types.is_numeric_dtype(df_map[color_col]):
    df_map["tCO2e"] = np.log10(df_map[color_col])
    color_to_use = "tCO2e"
    # compute robust color limits (1st to 99th percentile)
    vmin = df_map["tCO2e"].quantile(0.01)
    vmax = df_map["tCO2e"].quantile(0.99)
else:
    color_to_use = color_col
    vmin = None
    vmax = None

fig = px.scatter_mapbox(
    df_map,
    lat="Latitude",
    lon="Longitude",
    color=color_to_use,
    color_continuous_scale="Plasma",   # change to any other scale: 'Turbo', 'Plasma', etc.
    range_color=[vmin, vmax] if (vmin is not None and vmax is not None) else None,
    hover_name=hover_cols[0] if hover_cols else None,
    hover_data=hover_cols[1:],
    animation_frame="Year" if "Year" in df_map.columns else None,
    zoom=5,
    center=center,
    height=1200,
    width=1200,
)

# tune marker appearance (opacity, size) and title
fig.update_traces(marker=dict(opacity=0.7, sizemode="area", sizeref=2, sizemin=4))
fig.update_layout(mapbox_style="open-street-map",
                  margin={"r":0,"t":30,"l":0,"b":0},
                  title="NAEI Point Sources by Year")

# if using log color, relabel colorbar to show original scale approx.
if color_to_use == "tCO2e" and color_col is not None:
    fig.update_coloraxes(colorbar_title=f"log10({color_col})")

fig.show()

## 1.1 Country Analysis
I built this tree diagram with a heavy hand from ChatGPT which is a great help for this kind of thing and helps understand what/who are the key polluters in the UK.

In [77]:
# pick source dataframe (use aggregated if present)
source_df = df_aggregated if 'df_aggregated' in globals() else df

max_gwp = float(source_df["Emissions_GWP"].max()) if not source_df["Emissions_GWP"].empty else 1.0
max_gwp = max(max_gwp, 1.0)

# find year column
year_candidates = ["Year", "Reporting Year", "Reporting_Year", "Year_of_Emission", "Emission Year"]
year_col = next((c for c in year_candidates if c in source_df.columns), None)
if year_col is None:
    # try to coerce a numeric 'Year' from any date-like column, else create a dummy
    year_col = "Year"
    source_df[year_col] = source_df.get(year_col, "All")

# find a region column (fallback to a single region "United Kingdom")
region_candidates = ["Region", "Country", "Nation", "Area", "RegionName", "CountryName"]
region_col = next((c for c in region_candidates if c in source_df.columns), None)
if region_col is None:
    source_df["Region"] = "United Kingdom"
    region_col = "Region"
    
# find sector column (fallback to synthetic 'Sector' with value 'All')
sector_candidates = ["Sector", "Activity", "SIC", "SectorName"]
sector_col = next((c for c in sector_candidates if c in source_df.columns), None)
if sector_col is None:
    source_df["Sector"] = "All"
    sector_col = "Sector"

# find a site/name column for the leaf level (fallbacks)
site_candidates = ["Site", "Site_Name", "Plant", "Plant_Name", "Name"]
site_col = next((c for c in site_candidates if c in source_df.columns), None)
if site_col is None:
    # use an index-based label if no site-like column exists
    source_df = source_df.reset_index().rename(columns={"index": "row_id"})
    site_col = "row_id"

# ensure Emissions_GWP exists and is numeric
if "Emissions_GWP" not in source_df.columns:
    source_df["Emissions_GWP"] = pd.to_numeric(source_df.get("Emission", 0), errors="coerce") * pd.to_numeric(source_df.get("GWP", 1), errors="coerce")
source_df["Emissions_GWP"] = pd.to_numeric(source_df["Emissions_GWP"], errors="coerce").fillna(0)

# prepare widget values
years = sorted(source_df[year_col].dropna().unique().tolist(), key=lambda x: str(x))
years = ["All"] + [str(y) for y in years]
regions = sorted(source_df[region_col].dropna().unique().tolist())
regions = ["All"] + regions
sectors = sorted(source_df[sector_col].dropna().unique().tolist())
sectors = ["All"] + [s for s in sectors if s != "All"]

year_widget = widgets.Dropdown(options=years, value=years[-1], description="Year")
region_widget = widgets.Dropdown(options=regions, value="All", description="Region")
sector_widget = widgets.Dropdown(options=sectors, value="All", description="Sector")

# threshold slider initialised with a sensible global max; we'll update it when year/region change
threshold_widget = widgets.FloatSlider(
    value=0.0,
    min=0.0,
    max=max_gwp,
    step=max_gwp/100.0,
    description="Min Emissions",
    readout_format=".1f",
    continuous_update=False
)

def compute_max_for_selection(year_val, region_val):
    df_sel = source_df
    if year_val != "All":
        df_sel = df_sel[df_sel[year_col].astype(str) == str(year_val)]
    if region_val != "All":
        df_sel = df_sel[df_sel[region_col] == region_val]
    if df_sel.empty:
        return 1.0
    m = df_sel["Emissions_GWP"].max()
    m = float(m) if pd.notna(m) else 0.0
    # ensure at least 1.0 to avoid zero-range slider
    return max(m, 1.0)

def update_threshold_range(change=None):
    # called when year or region widgets change
    year_val = year_widget.value
    region_val = region_widget.value
    new_max = compute_max_for_selection(year_val, region_val)
    # update slider properties
    threshold_widget.max = new_max
    threshold_widget.step = max(new_max / 100.0, 1e-6)
    # if current value is greater than the new max, clamp it
    if threshold_widget.value > new_max:
        threshold_widget.value = new_max

# attach observers so slider updates when user changes year or region
year_widget.observe(update_threshold_range, names="value")
region_widget.observe(update_threshold_range, names="value")

# call once to set initial range consistent with the default year/region
update_threshold_range()

def plot_tree(selected_year: str, selected_region: str, selected_sector: str, threshold: float = 0.0, log_color: bool = True):
    clear_output(wait=True)

    # base selection used to compute true region totals (year/region/sector BEFORE threshold)
    df_base = source_df.copy()
    if selected_year != "All":
        df_base = df_base[df_base[year_col].astype(str) == str(selected_year)]
    if selected_region != "All":
        df_base = df_base[df_base[region_col] == selected_region]
    if selected_sector != "All":
        df_base = df_base[df_base[sector_col] == selected_sector]

    # now the plotted dataframe (threshold applied)
    df_plot = df_base.copy()
    try:
        thr = float(threshold)
    except Exception:
        thr = 0.0
    before = len(df_plot)
    df_plot = df_plot[df_plot["Emissions_GWP"].astype(float) >= thr]
    after = len(df_plot)
    print(f"Filtered Emissions_GWP >= {thr}  —  rows before: {before}, after: {after}")

    if df_plot.empty:
        print("No data for selection after threshold filter.")
        return

    # aggregate to site-level so each treemap node has consistent customdata
    site_agg = df_plot.groupby([region_col, site_col], as_index=False).agg({
        "Emissions_GWP": "sum",
        sector_col: (lambda s: ",".join(sorted(set(s.dropna().astype(str)))))
    })

    # map region totals (from df_base) and compute pct_of_region on aggregated rows
    region_totals_series = df_base.groupby(region_col)["Emissions_GWP"].sum()
    site_agg["region_total"] = site_agg[region_col].map(region_totals_series).fillna(0.0)
    site_agg["pct_of_region"] = np.where(
        site_agg["region_total"] > 0,
        site_agg["Emissions_GWP"].astype(float) / site_agg["region_total"].astype(float) * 100.0,
        0.0
    )

    # color
    site_agg["_color"] = np.log10(site_agg["Emissions_GWP"].replace(0, np.nan)).fillna(0.0) if log_color else site_agg["Emissions_GWP"]

    # build treemap from aggregated dataframe - custom_data now matches nodes
    fig = px.treemap(
        site_agg,
        path=[region_col, site_col],
        values="pct_of_region",
        color="_color",
        color_continuous_scale="Plasma",
        custom_data=[sector_col, "region_total", "Emissions_GWP"],
        title=f"Emissions (% of region) — Year={selected_year}, Region={selected_region}, Sector={selected_sector}, Min={thr}",
        height=800,
        width=1400,
    )

    if log_color:
        fig.update_coloraxes(colorbar_title="log10(Emissions_GWP)")

    fig.update_traces(
        root_color="lightgray",
        hovertemplate=(
            '%{label}<br>Percentage of region: %{value:.2f}%<br>'
            'Sector(s): %{customdata[0]}<br>Region total: %{customdata[1]:.2f}<br>'
            'Site Emissions: %{customdata[2]:.2f}<extra></extra>'
        )
    )

    fig.show()

# include sector_widget in the UI and interactive mapping
ui = widgets.HBox([year_widget, region_widget, sector_widget, threshold_widget])
out = widgets.interactive_output(plot_tree, {
    "selected_year": year_widget,
    "selected_region": region_widget,
    "selected_sector": sector_widget,
    "threshold": threshold_widget
})
display(ui, out)


Output()